# Individual S&ML Project - Kaggle Challenge

Code by: ***Jorge Polanco***

In [ ]:
#install.packages("woeBinning")
#install.packages("bartMachine")
#install.packages("car")
#install.packages("foreign")
#install.packages('refund')

In [3]:
# Importing libraries
library(randomForest)
library(bartMachine)
library(data.table)
library(woeBinning)
library(tidyverse)
library(reshape2)
library(ggplot2)
library(xgboost)
library(foreign)
library(refund)
library(caret)
library(pROC)
library(tree)
library(mlr)
library(gbm)
library(car)

## 1) Data Engineering

**a) Loading the datasets:**

In [4]:
train = read.csv(file = "C:/Users/jpolancoroque/Desktop/IESEG/02. Second Semester/Statistical & Machine Learning Approaches for Marketing/Kaggle/kaggle_data/bank_mkt_train.csv")
test = read.csv(file = "C:/Users/jpolancoroque/Desktop/IESEG/02. Second Semester/Statistical & Machine Learning Approaches for Marketing/Kaggle/kaggle_data/bank_mkt_test.csv")

**b) Creating categories:**

Binning Job Feature:

In [5]:
# Grouping 12 categories in the variable job onto 3 groups using WOE
binning_cat = woe.binning(train, 'subscribe', 'job')

# Apply the binning to the train data
train = woe.binning.deploy(train, binning_cat)

# Apply the binning to the test (holdout) data
test = woe.binning.deploy(test, binning_cat)

Binning Age Feature:

In [6]:
# TRAIN
# Changing age variable
train$age.18to25[train$age <= 25] = 1
train$age.18to25[is.na(train$age.18to25)] = 0

train$age.26to35[train$age <= 35 & train$age > 25 ] = 1
train$age.26to35[is.na(train$age.26to35)] = 0

train$age.36to45[train$age <= 45 & train$age > 35 ] = 1
train$age.36to45[is.na(train$age.36to45)] = 0

train$age.46to60[train$age <= 60 & train$age > 45 ] = 1
train$age.46to60[is.na(train$age.46to60)] = 0

train$age.61to75[train$age <= 75 & train$age > 61 ] = 1
train$age.61to75[is.na(train$age.61to75)] = 0

train$age.plus76[train$age > 75] = 1
train$age.plus76[is.na(train$age.plus76)] = 0

####################

# TEST
# Changing age variable

test$age.18to25[test$age <= 25] = 1
test$age.18to25[is.na(test$age.18to25)] = 0

test$age.26to35[test$age <= 35 & test$age > 25 ] = 1
test$age.26to35[is.na(test$age.26to35)] = 0

test$age.36to45[test$age <= 45 & test$age > 35 ] = 1
test$age.36to45[is.na(test$age.36to45)] = 0

test$age.46to60[test$age <= 60 & test$age > 45 ] = 1
test$age.46to60[is.na(test$age.46to60)] = 0

test$age.61to75[test$age <= 75 & test$age > 61 ] = 1
test$age.61to75[is.na(test$age.61to75)] = 0

test$age.plus76[test$age > 75] = 1
test$age.plus76[is.na(test$age.plus76)] = 0

Seasons:

In [7]:
## TRAIN
# Spring
train$spring[train$month == 'mar' | train$month =='apr'  | train$month == 'may'] = 1
train$spring[is.na(train$spring)] = 0

# Summer
train$summer[train$month == 'jun' | train$month =='jul'  | train$month == 'aug'] = 1
train$summer[is.na(train$summer)] = 0

# Autumn
train$autumn[train$month == 'sep' | train$month =='oct'  | train$month == 'nov'] = 1
train$autumn[is.na(train$autumn)] = 0

# Winter
train$winter[train$month == 'dec' | train$month =='jan'  | train$month == 'feb'] = 1
train$winter[is.na(train$winter)] = 0

## TEST
# Spring
test$spring[test$month == 'mar' | test$month =='apr'  | test$month == 'may'] = 1
test$spring[is.na(test$spring)] = 0

# Summer
test$summer[test$month == 'jun' | test$month =='jul'  | test$month == 'aug'] = 1
test$summer[is.na(test$summer)] = 0

# Autumn
test$autumn[test$month == 'sep' | test$month =='oct'  | test$month == 'nov'] = 1
test$autumn[is.na(test$autumn)] = 0

# Winter
test$winter[test$month == 'dec' | test$month =='jan'  | test$month == 'feb'] = 1
test$winter[is.na(test$winter)] = 0

Quarters:

In [8]:
## TRAIN
# Q1
train$Q1[train$month == 'jan' | train$month =='feb'  | train$month == 'mar'] = 1
train$Q1[is.na(train$Q1)] = 0

# Q2
train$Q2[train$month == 'apr' | train$month =='may'  | train$month == 'jun'] = 1
train$Q2[is.na(train$Q2)] = 0

# Q3
train$Q3[train$month == 'jul' | train$month =='aug'  | train$month == 'sep'] = 1
train$Q3[is.na(train$Q3)] = 0

# Q4
train$Q4[train$month == 'oct' | train$month =='nov'  | train$month == 'dec'] = 1
train$Q4[is.na(train$Q4)] = 0

## TEST
# Q1
test$Q1[test$month == 'jan' | test$month =='feb'  | test$month == 'mar'] = 1
test$Q1[is.na(test$Q1)] = 0

# Q2
test$Q2[test$month == 'apr' | test$month =='may'  | test$month == 'jun'] = 1
test$Q2[is.na(test$Q2)] = 0

# Q3
test$Q3[test$month == 'jul' | test$month =='aug'  | test$month == 'sep'] = 1
test$Q3[is.na(test$Q3)] = 0

# Q4
test$Q4[test$month == 'oct' | test$month =='nov'  | test$month == 'dec'] = 1
test$Q4[is.na(test$Q4)] = 0

Campaing Segments:

In [9]:
# TRAIN
# Changing campaing variable
train$campaing.le_5[train$campaign <= 5] = 1
train$campaing.le_5[is.na(train$campaing.le_5)] = 0

train$campaing.6to10[train$campaign <= 10 & train$campaign > 5] = 1
train$campaing.6to10[is.na(train$campaing.6to10)] = 0

train$campaing.11to15[train$campaign <= 15 & train$campaign > 10] = 1
train$campaing.11to15[is.na(train$campaing.11to15)] = 0

train$campaing.16to20[train$campaign <= 20 & train$campaign > 15] = 1
train$campaing.16to20[is.na(train$campaing.16to20)] = 0

train$campaing.21to25[train$campaign <= 25 & train$campaign > 20] = 1
train$campaing.21to25[is.na(train$campaing.21to25)] = 0

train$campaing.26to30[train$campaign <= 30 & train$campaign > 25] = 1
train$campaing.26to30[is.na(train$campaing.26to30)] = 0

train$campaing.30to35[train$campaign <= 35 & train$campaign > 30] = 1
train$campaing.30to35[is.na(train$campaing.30to35)] = 0

####################

# TEST
# Changing campaing variable
test$campaing.le_5[test$campaign <= 5] = 1
test$campaing.le_5[is.na(test$campaing.le_5)] = 0

test$campaing.6to10[test$campaign <= 10 & test$campaign > 5] = 1
test$campaing.6to10[is.na(test$campaing.6to10)] = 0

test$campaing.11to15[test$campaign <= 15 & test$campaign > 10] = 1
test$campaing.11to15[is.na(test$campaing.11to15)] = 0

test$campaing.16to20[test$campaign <= 20 & test$campaign > 15] = 1
test$campaing.16to20[is.na(test$campaing.16to20)] = 0

test$campaing.21to25[test$campaign <= 25 & test$campaign > 20] = 1
test$campaing.21to25[is.na(test$campaing.21to25)] = 0

test$campaing.26to30[test$campaign <= 30 & test$campaign > 25] = 1
test$campaing.26to30[is.na(test$campaing.26to30)] = 0

test$campaing.30to35[test$campaign <= 35 & test$campaign > 30] = 1
test$campaing.30to35[is.na(test$campaing.30to35)] = 0

Pday Features:

In [10]:
# TRAIN
# Changing pday variable
train$pdays.0to10[train$pdays <= 10] = 1
train$pdays.0to10[is.na(train$pdays.0to10)] = 0

train$pdays.11to20[train$pdays <= 20 & train$pdays > 10] = 1
train$pdays.11to20[is.na(train$pdays.11to20)] = 0

train$pdays.999[train$pdays > 20] = 1
train$pdays.999[is.na(train$pdays.999)] = 0

####################

# TEST
# Changing pday variable
test$pdays.0to10[test$pdays <= 10] = 1
test$pdays.0to10[is.na(test$pdays.0to10)] = 0

test$pdays.11to20[test$pdays <= 20 & test$pdays > 10] = 1
test$pdays.11to20[is.na(test$pdays.11to20)] = 0

test$pdays.999[test$pdays > 20] = 1
test$pdays.999[is.na(test$pdays.999)] = 0

Previous Features:

In [11]:
# TRAIN
# Changing previous variable
train$previous.1to3[train$previous <= 3] = 1
train$previous.1to3[is.na(train$previous.1to3)] = 0

train$previous.4to6[train$previous > 3] = 1
train$previous.4to6[is.na(train$previous.4to6)] = 0

####################

# TEST
# Changing previous variable
test$previous.1to3[test$previous <= 3] = 1
test$previous.1to3[is.na(test$previous.1to3)] = 0

test$previous.4to6[test$previous > 3] = 1
test$previous.4to6[is.na(test$previous.4to6)] = 0

Emp. Features:

In [12]:
# TRAIN
# Changing emp.var.rate variable
train$emp.var.rate.pos[train$emp.var.rate > 0] = 1
train$emp.var.rate.pos[is.na(train$emp.var.rate.pos)] = 0

train$emp.var.rate.neg[train$emp.var.rate < 0] = 1
train$emp.var.rate.neg[is.na(train$emp.var.rate.neg)] = 0

####################

# TEST
# Changing emp.var.rate variable
test$emp.var.rate.pos[test$emp.var.rate > 0] = 1
test$emp.var.rate.pos[is.na(test$emp.var.rate.pos)] = 0

test$emp.var.rate.neg[test$emp.var.rate < 0] = 1
test$emp.var.rate.neg[is.na(test$emp.var.rate.neg)] = 0

**c) Dummification of Categories:**

In [13]:
# TRAIN
# Creating new features
dmy = dummyVars(" ~ .", data = train)
train_df = data.frame(predict(dmy, newdata = train))

####################

# TEST
# Creating new features
dmy2 = dummyVars(" ~ .", data = test)
test_df = data.frame(predict(dmy2, newdata = test))

**d) Factorizing the dependent variable:**

In [14]:
train_df$subscribe = as.factor(train_df$subscribe)

In [15]:
train_df2 = train_df
test_df2 = test_df

**e) Creating metrics:**

Price Index by Age:

In [16]:
# TRAIN
# Creating Mean cons.price.idx_mean
train_df2$cons.price.idx_mean_1[train_df2$age <= 25] = mean(train_df2$cons.price.idx[train_df2$age <= 25])
train_df2$cons.price.idx_mean_1[is.na(train_df2$cons.price.idx_mean_1)] = 0

train_df2$cons.price.idx_mean_2[train_df2$age <= 35 & train_df2$age > 25 ] = mean(train_df2$cons.price.idx[train_df2$age <= 35 & train_df2$age > 25 ])
train_df2$cons.price.idx_mean_2[is.na(train_df2$cons.price.idx_mean_2)] = 0

train_df2$cons.price.idx_mean_3[train_df2$age <= 45 & train_df2$age > 35 ] = mean(train_df2$cons.price.idx[train_df2$age <= 45 & train_df2$age > 35 ])
train_df2$cons.price.idx_mean_3[is.na(train_df2$cons.price.idx_mean_3)] = 0

train_df2$cons.price.idx_mean_4[train_df2$age <= 60 & train_df2$age > 45 ] = mean(train_df2$cons.price.idx[train_df2$age <= 60 & train_df2$age > 45 ])
train_df2$cons.price.idx_mean_4[is.na(train_df2$cons.price.idx_mean_4)] = 0

train_df2$cons.price.idx_mean_5[train_df2$age <= 75 & train_df2$age > 61 ] = mean(train_df2$cons.price.idx[train_df2$age <= 75 & train_df2$age > 61 ])
train_df2$cons.price.idx_mean_5[is.na(train_df2$cons.price.idx_mean_5)] = 0

train_df2$cons.price.idx_mean_6[train_df2$age > 75] = mean(train_df2$cons.price.idx[train_df2$age > 75])
train_df2$cons.price.idx_mean_6[is.na(train_df2$cons.price.idx_mean_6)] = 0

train_df2$cons.price.idx_mean = train_df2$cons.price.idx_mean_1+train_df2$cons.price.idx_mean_2+train_df2$cons.price.idx_mean_3+train_df2$cons.price.idx_mean_4+train_df2$cons.price.idx_mean_5+train_df2$cons.price.idx_mean_6

####################

# TEST
# Creating Mean cons.price.idx_mean
test_df2$cons.price.idx_mean_1[test_df2$age <= 25] = mean(test_df2$cons.price.idx[test_df2$age <= 25])
test_df2$cons.price.idx_mean_1[is.na(test_df2$cons.price.idx_mean_1)] = 0

test_df2$cons.price.idx_mean_2[test_df2$age <= 35 & test_df2$age > 25 ] = mean(test_df2$cons.price.idx[test_df2$age <= 35 & test_df2$age > 25 ])
test_df2$cons.price.idx_mean_2[is.na(test_df2$cons.price.idx_mean_2)] = 0

test_df2$cons.price.idx_mean_3[test_df2$age <= 45 & test_df2$age > 35 ] = mean(test_df2$cons.price.idx[test_df2$age <= 45 & test_df2$age > 35 ])
test_df2$cons.price.idx_mean_3[is.na(test_df2$cons.price.idx_mean_3)] = 0

test_df2$cons.price.idx_mean_4[test_df2$age <= 60 & test_df2$age > 45 ] = mean(test_df2$cons.price.idx[test_df2$age <= 60 & test_df2$age > 45 ])
test_df2$cons.price.idx_mean_4[is.na(test_df2$cons.price.idx_mean_4)] = 0

test_df2$cons.price.idx_mean_5[test_df2$age <= 75 & test_df2$age > 61 ] = mean(test_df2$cons.price.idx[test_df2$age <= 75 & test_df2$age > 61 ])
test_df2$cons.price.idx_mean_5[is.na(test_df2$cons.price.idx_mean_5)] = 0

test_df2$cons.price.idx_mean_6[test_df2$age > 75] = mean(test_df2$cons.price.idx[test_df2$age > 75])
test_df2$cons.price.idx_mean_6[is.na(test_df2$cons.price.idx_mean_6)] = 0

test_df2$cons.price.idx_mean = test_df2$cons.price.idx_mean_1+test_df2$cons.price.idx_mean_2+test_df2$cons.price.idx_mean_3+test_df2$cons.price.idx_mean_4+test_df2$cons.price.idx_mean_5+test_df2$cons.price.idx_mean_6

Euribor by Age:

In [17]:
# TRAIN
# Creating Mean euribor3m
train_df2$euribor3m_mean_1[train_df2$age <= 25] = mean(train_df2$euribor3m[train_df2$age <= 25])
train_df2$euribor3m_mean_1[is.na(train_df2$euribor3m_mean_1)] = 0

train_df2$euribor3m_mean_2[train_df2$age <= 35 & train_df2$age > 25 ] = mean(train_df2$euribor3m[train_df2$age <= 35 & train_df2$age > 25 ])
train_df2$euribor3m_mean_2[is.na(train_df2$euribor3m_mean_2)] = 0

train_df2$euribor3m_mean_3[train_df2$age <= 45 & train_df2$age > 35 ] = mean(train_df2$euribor3m[train_df2$age <= 45 & train_df2$age > 35 ])
train_df2$euribor3m_mean_3[is.na(train_df2$euribor3m_mean_3)] = 0

train_df2$euribor3m_mean_4[train_df2$age <= 60 & train_df2$age > 45 ] = mean(train_df2$euribor3m[train_df2$age <= 60 & train_df2$age > 45 ])
train_df2$euribor3m_mean_4[is.na(train_df2$euribor3m_mean_4)] = 0

train_df2$euribor3m_mean_5[train_df2$age <= 75 & train_df2$age > 61 ] = mean(train_df2$euribor3m[train_df2$age <= 75 & train_df2$age > 61 ])
train_df2$euribor3m_mean_5[is.na(train_df2$euribor3m_mean_5)] = 0

train_df2$euribor3m_mean_6[train_df2$age > 75] = mean(train_df2$euribor3m[train_df2$age > 75])
train_df2$euribor3m_mean_6[is.na(train_df2$euribor3m_mean_6)] = 0

train_df2$euribor3m_mean = train_df2$euribor3m_mean_1+train_df2$euribor3m_mean_2+train_df2$euribor3m_mean_3+train_df2$euribor3m_mean_4+train_df2$euribor3m_mean_5+train_df2$euribor3m_mean_6

####################

# TEST
# Creating Mean euribor3m
test_df2$euribor3m_mean_1[test_df2$age <= 25] = mean(test_df2$euribor3m[test_df2$age <= 25])
test_df2$euribor3m_mean_1[is.na(test_df2$euribor3m_mean_1)] = 0

test_df2$euribor3m_mean_2[test_df2$age <= 35 & test_df2$age > 25 ] = mean(test_df2$euribor3m[test_df2$age <= 35 & test_df2$age > 25 ])
test_df2$euribor3m_mean_2[is.na(test_df2$euribor3m_mean_2)] = 0

test_df2$euribor3m_mean_3[test_df2$age <= 45 & test_df2$age > 35 ] = mean(test_df2$euribor3m[test_df2$age <= 45 & test_df2$age > 35 ])
test_df2$euribor3m_mean_3[is.na(test_df2$euribor3m_mean_3)] = 0

test_df2$euribor3m_mean_4[test_df2$age <= 60 & test_df2$age > 45 ] = mean(test_df2$euribor3m[test_df2$age <= 60 & test_df2$age > 45 ])
test_df2$euribor3m_mean_4[is.na(test_df2$euribor3m_mean_4)] = 0

test_df2$euribor3m_mean_5[test_df2$age <= 75 & test_df2$age > 61 ] = mean(test_df2$euribor3m[test_df2$age <= 75 & test_df2$age > 61 ])
test_df2$euribor3m_mean_5[is.na(test_df2$euribor3m_mean_5)] = 0

test_df2$euribor3m_mean_6[test_df2$age > 75] = mean(test_df2$euribor3m[test_df2$age > 75])
test_df2$euribor3m_mean_6[is.na(test_df2$euribor3m_mean_6)] = 0

test_df2$euribor3m_mean = test_df2$euribor3m_mean_1+test_df2$euribor3m_mean_2+test_df2$euribor3m_mean_3+test_df2$euribor3m_mean_4+test_df2$euribor3m_mean_5+test_df2$euribor3m_mean_6

In [18]:
# TRAIN
# Creating Max euribor3m
train_df2$euribor3m_max_1[train_df2$age <= 25] = max(train_df2$euribor3m[train_df2$age <= 25])
train_df2$euribor3m_max_1[is.na(train_df2$euribor3m_max_1)] = 0

train_df2$euribor3m_max_2[train_df2$age <= 35 & train_df2$age > 25 ] = max(train_df2$euribor3m[train_df2$age <= 35 & train_df2$age > 25 ])
train_df2$euribor3m_max_2[is.na(train_df2$euribor3m_max_2)] = 0

train_df2$euribor3m_max_3[train_df2$age <= 45 & train_df2$age > 35 ] = max(train_df2$euribor3m[train_df2$age <= 45 & train_df2$age > 35 ])
train_df2$euribor3m_max_3[is.na(train_df2$euribor3m_max_3)] = 0

train_df2$euribor3m_max_4[train_df2$age <= 60 & train_df2$age > 45 ] = max(train_df2$euribor3m[train_df2$age <= 60 & train_df2$age > 45 ])
train_df2$euribor3m_max_4[is.na(train_df2$euribor3m_max_4)] = 0

train_df2$euribor3m_max_5[train_df2$age <= 75 & train_df2$age > 61 ] = max(train_df2$euribor3m[train_df2$age <= 75 & train_df2$age > 61 ])
train_df2$euribor3m_max_5[is.na(train_df2$euribor3m_max_5)] = 0

train_df2$euribor3m_max_6[train_df2$age > 75] = max(train_df2$euribor3m[train_df2$age > 75])
train_df2$euribor3m_max_6[is.na(train_df2$euribor3m_max_6)] = 0

train_df2$euribor3m_max = train_df2$euribor3m_max_1+train_df2$euribor3m_max_2+train_df2$euribor3m_max_3+train_df2$euribor3m_max_4+train_df2$euribor3m_max_5+train_df2$euribor3m_max_6

####################

# TEST
# Creating Max euribor3m
test_df2$euribor3m_max_1[test_df2$age <= 25] = max(test_df2$euribor3m[test_df2$age <= 25])
test_df2$euribor3m_max_1[is.na(test_df2$euribor3m_max_1)] = 0

test_df2$euribor3m_max_2[test_df2$age <= 35 & test_df2$age > 25 ] = max(test_df2$euribor3m[test_df2$age <= 35 & test_df2$age > 25 ])
test_df2$euribor3m_max_2[is.na(test_df2$euribor3m_max_2)] = 0

test_df2$euribor3m_max_3[test_df2$age <= 45 & test_df2$age > 35 ] = max(test_df2$euribor3m[test_df2$age <= 45 & test_df2$age > 35 ])
test_df2$euribor3m_max_3[is.na(test_df2$euribor3m_max_3)] = 0

test_df2$euribor3m_max_4[test_df2$age <= 60 & test_df2$age > 45 ] = max(test_df2$euribor3m[test_df2$age <= 60 & test_df2$age > 45 ])
test_df2$euribor3m_max_4[is.na(test_df2$euribor3m_max_4)] = 0

test_df2$euribor3m_max_5[test_df2$age <= 75 & test_df2$age > 61 ] = max(test_df2$euribor3m[test_df2$age <= 75 & test_df2$age > 61 ])
test_df2$euribor3m_max_5[is.na(test_df2$euribor3m_max_5)] = 0

test_df2$euribor3m_max_6[test_df2$age > 75] = max(test_df2$euribor3m[test_df2$age > 75])
test_df2$euribor3m_max_6[is.na(test_df2$euribor3m_max_6)] = 0

test_df2$euribor3m_max = test_df2$euribor3m_max_1+test_df2$euribor3m_max_2+test_df2$euribor3m_max_3+test_df2$euribor3m_max_4+test_df2$euribor3m_max_5+test_df2$euribor3m_max_6

In [19]:
# TRAIN
# Creating Min euribor3m
train_df2$euribor3m_min_1[train_df2$age <= 25] = min(train_df2$euribor3m[train_df2$age <= 25])
train_df2$euribor3m_min_1[is.na(train_df2$euribor3m_min_1)] = 0

train_df2$euribor3m_min_2[train_df2$age <= 35 & train_df2$age > 25 ] = min(train_df2$euribor3m[train_df2$age <= 35 & train_df2$age > 25 ])
train_df2$euribor3m_min_2[is.na(train_df2$euribor3m_min_2)] = 0

train_df2$euribor3m_min_3[train_df2$age <= 45 & train_df2$age > 35 ] = min(train_df2$euribor3m[train_df2$age <= 45 & train_df2$age > 35 ])
train_df2$euribor3m_min_3[is.na(train_df2$euribor3m_min_3)] = 0

train_df2$euribor3m_min_4[train_df2$age <= 60 & train_df2$age > 45 ] = min(train_df2$euribor3m[train_df2$age <= 60 & train_df2$age > 45 ])
train_df2$euribor3m_min_4[is.na(train_df2$euribor3m_min_4)] = 0

train_df2$euribor3m_min_5[train_df2$age <= 75 & train_df2$age > 61 ] = min(train_df2$euribor3m[train_df2$age <= 75 & train_df2$age > 61 ])
train_df2$euribor3m_min_5[is.na(train_df2$euribor3m_min_5)] = 0

train_df2$euribor3m_min_6[train_df2$age > 75] = min(train_df2$euribor3m[train_df2$age > 75])
train_df2$euribor3m_min_6[is.na(train_df2$euribor3m_min_6)] = 0

train_df2$euribor3m_min = train_df2$euribor3m_min_1+train_df2$euribor3m_min_2+train_df2$euribor3m_min_3+train_df2$euribor3m_min_4+train_df2$euribor3m_min_5+train_df2$euribor3m_min_6

####################

# TEST
# Creating Min euribor3m
test_df2$euribor3m_min_1[test_df2$age <= 25] = min(test_df2$euribor3m[test_df2$age <= 25])
test_df2$euribor3m_min_1[is.na(test_df2$euribor3m_min_1)] = 0

test_df2$euribor3m_min_2[test_df2$age <= 35 & test_df2$age > 25 ] = min(test_df2$euribor3m[test_df2$age <= 35 & test_df2$age > 25 ])
test_df2$euribor3m_min_2[is.na(test_df2$euribor3m_min_2)] = 0

test_df2$euribor3m_min_3[test_df2$age <= 45 & test_df2$age > 35 ] = min(test_df2$euribor3m[test_df2$age <= 45 & test_df2$age > 35 ])
test_df2$euribor3m_min_3[is.na(test_df2$euribor3m_min_3)] = 0

test_df2$euribor3m_min_4[test_df2$age <= 60 & test_df2$age > 45 ] = min(test_df2$euribor3m[test_df2$age <= 60 & test_df2$age > 45 ])
test_df2$euribor3m_min_4[is.na(test_df2$euribor3m_min_4)] = 0

test_df2$euribor3m_min_5[test_df2$age <= 75 & test_df2$age > 61 ] = min(test_df2$euribor3m[test_df2$age <= 75 & test_df2$age > 61 ])
test_df2$euribor3m_min_5[is.na(test_df2$euribor3m_min_5)] = 0

test_df2$euribor3m_min_6[test_df2$age > 75] = min(test_df2$euribor3m[test_df2$age > 75])
test_df2$euribor3m_min_6[is.na(test_df2$euribor3m_min_6)] = 0

test_df2$euribor3m_min = test_df2$euribor3m_min_1+test_df2$euribor3m_min_2+test_df2$euribor3m_min_3+test_df2$euribor3m_min_4+test_df2$euribor3m_min_5+test_df2$euribor3m_min_6

Price Index by Job:

In [20]:
# Creating Mean job
train_df2$cpi_mean_admin[train_df2$job.admin. == 1] = mean(train_df2$cons.price.idx[train_df2$job.admin. == 1])
train_df2$cpi_mean_admin[is.na(train_df2$cpi_mean_admin)] = 0

train_df2$cpi_mean_bc[train_df2$job.blue.collar == 1] = mean(train_df2$cons.price.idx[train_df2$job.blue.collar == 1])
train_df2$cpi_mean_bc[is.na(train_df2$cpi_mean_bc)] = 0

train_df2$cpi_mean_u[train_df2$job.unemployed == 1] = mean(train_df2$cons.price.idx[train_df2$job.unemployed == 1])
train_df2$cpi_mean_u[is.na(train_df2$cpi_mean_u)] = 0

train_df2$cpi_mean_t[train_df2$job.technician == 1] = mean(train_df2$cons.price.idx[train_df2$job.technician == 1])
train_df2$cpi_mean_t[is.na(train_df2$cpi_mean_t)] = 0

train_df2$cpi_mean_stu[train_df2$job.student == 1] = mean(train_df2$cons.price.idx[train_df2$job.student == 1])
train_df2$cpi_mean_stu[is.na(train_df2$cpi_mean_stu)] = 0

train_df2$cpi_mean_se[train_df2$job.self.employed == 1] = mean(train_df2$cons.price.idx[train_df2$job.self.employed == 1])
train_df2$cpi_mean_se[is.na(train_df2$cpi_mean_se)] = 0

train_df2$cpi_mean_man[train_df2$job.management == 1] = mean(train_df2$cons.price.idx[train_df2$job.management == 1])
train_df2$cpi_mean_man[is.na(train_df2$cpi_mean_man)] = 0

train_df2$cpi_mean_ent[train_df2$job.entrepreneur == 1] = mean(train_df2$cons.price.idx[train_df2$job.entrepreneur == 1])
train_df2$cpi_mean_ent[is.na(train_df2$cpi_mean_ent)] = 0

train_df2$cpi_mean_unk[train_df2$job.unknown == 1] = mean(train_df2$cons.price.idx[train_df2$job.unknown == 1])
train_df2$cpi_mean_unk[is.na(train_df2$cpi_mean_unk)] = 0

train_df2$cpi_mean_ret[train_df2$job.retired == 1] = mean(train_df2$cons.price.idx[train_df2$job.retired == 1])
train_df2$cpi_mean_ret[is.na(train_df2$cpi_mean_ret)] = 0

train_df2$cpi_mean_ser[train_df2$job.services == 1] = mean(train_df2$cons.price.idx[train_df2$job.services == 1])
train_df2$cpi_mean_ser[is.na(train_df2$cpi_mean_ser)] = 0

train_df2$cpi_mean_hou[train_df2$job.housemaid == 1] = mean(train_df2$cons.price.idx[train_df2$job.housemaid == 1])
train_df2$cpi_mean_hou[is.na(train_df2$cpi_mean_hou)] = 0

train_df2$cpi_mean = train_df2$cpi_mean_admin + train_df2$cpi_mean_bc + train_df2$cpi_mean_u + train_df2$cpi_mean_t + train_df2$

cpi_mean_stu + train_df2$cpi_mean_se + train_df2$cpi_mean_man + train_df2$cpi_mean_ent + train_df2$cpi_mean_unk + train_df2$cpi_mean_ret + train_df2$cpi_mean_ser + train_df2$cpi_mean_hou

####################

# TEST
test_df2$cpi_mean_admin[test_df2$job.admin. == 1] = mean(test_df2$cons.price.idx[test_df2$job.admin. == 1])
test_df2$cpi_mean_admin[is.na(test_df2$cpi_mean_admin)] = 0

test_df2$cpi_mean_bc[test_df2$job.blue.collar == 1] = mean(test_df2$cons.price.idx[test_df2$job.blue.collar == 1])
test_df2$cpi_mean_bc[is.na(test_df2$cpi_mean_bc)] = 0

test_df2$cpi_mean_u[test_df2$job.unemployed == 1] = mean(test_df2$cons.price.idx[test_df2$job.unemployed == 1])
test_df2$cpi_mean_u[is.na(test_df2$cpi_mean_u)] = 0

test_df2$cpi_mean_t[test_df2$job.technician == 1] = mean(test_df2$cons.price.idx[test_df2$job.technician == 1])
test_df2$cpi_mean_t[is.na(test_df2$cpi_mean_t)] = 0

test_df2$cpi_mean_stu[test_df2$job.student == 1] = mean(test_df2$cons.price.idx[test_df2$job.student == 1])
test_df2$cpi_mean_stu[is.na(test_df2$cpi_mean_stu)] = 0

test_df2$cpi_mean_se[test_df2$job.self.employed == 1] = mean(test_df2$cons.price.idx[test_df2$job.self.employed == 1])
test_df2$cpi_mean_se[is.na(test_df2$cpi_mean_se)] = 0

test_df2$cpi_mean_man[test_df2$job.management == 1] = mean(test_df2$cons.price.idx[test_df2$job.management == 1])
test_df2$cpi_mean_man[is.na(test_df2$cpi_mean_man)] = 0

test_df2$cpi_mean_ent[test_df2$job.entrepreneur == 1] = mean(test_df2$cons.price.idx[test_df2$job.entrepreneur == 1])
test_df2$cpi_mean_ent[is.na(test_df2$cpi_mean_ent)] = 0

test_df2$cpi_mean_unk[test_df2$job.unknown == 1] = mean(test_df2$cons.price.idx[test_df2$job.unknown == 1])
test_df2$cpi_mean_unk[is.na(test_df2$cpi_mean_unk)] = 0

test_df2$cpi_mean_ret[test_df2$job.retired == 1] = mean(test_df2$cons.price.idx[test_df2$job.retired == 1])
test_df2$cpi_mean_ret[is.na(test_df2$cpi_mean_ret)] = 0

test_df2$cpi_mean_ser[test_df2$job.services == 1] = mean(test_df2$cons.price.idx[test_df2$job.services == 1])
test_df2$cpi_mean_ser[is.na(test_df2$cpi_mean_ser)] = 0

test_df2$cpi_mean_hou[test_df2$job.housemaid == 1] = mean(test_df2$cons.price.idx[test_df2$job.housemaid == 1])
test_df2$cpi_mean_hou[is.na(test_df2$cpi_mean_hou)] = 0

test_df2$cpi_mean = test_df2$cpi_mean_admin + test_df2$cpi_mean_bc + test_df2$cpi_mean_u + test_df2$cpi_mean_t + test_df2$

cpi_mean_stu + test_df2$cpi_mean_se + test_df2$cpi_mean_man + test_df2$cpi_mean_ent + test_df2$cpi_mean_unk + test_df2$cpi_mean_ret + test_df2$cpi_mean_ser + test_df2$cpi_mean_hou

Euribor by Job:

In [21]:
# TRAIN
# Creating Mean job
train_df2$euro_mean_admin[train_df2$job.admin. == 1] = mean(train_df2$euribor3m[train_df2$job.admin. == 1])
train_df2$euro_mean_admin[is.na(train_df2$euro_mean_admin)] = 0

train_df2$euro_mean_bc[train_df2$job.blue.collar == 1] = mean(train_df2$euribor3m[train_df2$job.blue.collar == 1])
train_df2$euro_mean_bc[is.na(train_df2$euro_mean_bc)] = 0

train_df2$euro_mean_u[train_df2$job.unemployed == 1] = mean(train_df2$euribor3m[train_df2$job.unemployed == 1])
train_df2$euro_mean_u[is.na(train_df2$euro_mean_u)] = 0

train_df2$euro_mean_t[train_df2$job.technician == 1] = mean(train_df2$euribor3m[train_df2$job.technician == 1])
train_df2$euro_mean_t[is.na(train_df2$euro_mean_t)] = 0

train_df2$euro_mean_stu[train_df2$job.student == 1] = mean(train_df2$euribor3m[train_df2$job.student == 1])
train_df2$euro_mean_stu[is.na(train_df2$euro_mean_stu)] = 0

train_df2$euro_mean_se[train_df2$job.self.employed == 1] = mean(train_df2$euribor3m[train_df2$job.self.employed == 1])
train_df2$euro_mean_se[is.na(train_df2$euro_mean_se)] = 0

train_df2$euro_mean_man[train_df2$job.management == 1] = mean(train_df2$euribor3m[train_df2$job.management == 1])
train_df2$euro_mean_man[is.na(train_df2$euro_mean_man)] = 0

train_df2$euro_mean_ent[train_df2$job.entrepreneur == 1] = mean(train_df2$euribor3m[train_df2$job.entrepreneur == 1])
train_df2$euro_mean_ent[is.na(train_df2$euro_mean_ent)] = 0

train_df2$euro_mean_unk[train_df2$job.unknown == 1] = mean(train_df2$euribor3m[train_df2$job.unknown == 1])
train_df2$euro_mean_unk[is.na(train_df2$euro_mean_unk)] = 0

train_df2$euro_mean_ret[train_df2$job.retired == 1] = mean(train_df2$euribor3m[train_df2$job.retired == 1])
train_df2$euro_mean_ret[is.na(train_df2$euro_mean_ret)] = 0

train_df2$euro_mean_ser[train_df2$job.services == 1] = mean(train_df2$euribor3m[train_df2$job.services == 1])
train_df2$euro_mean_ser[is.na(train_df2$euro_mean_ser)] = 0

train_df2$euro_mean_hou[train_df2$job.housemaid == 1] = mean(train_df2$euribor3m[train_df2$job.housemaid == 1])
train_df2$euro_mean_hou[is.na(train_df2$euro_mean_hou)] = 0

train_df2$euro_mean = train_df2$euro_mean_admin + train_df2$euro_mean_bc + train_df2$euro_mean_u + train_df2$euro_mean_t + train_df2$euro_mean_stu + train_df2$euro_mean_se + train_df2$euro_mean_man + train_df2$euro_mean_ent + train_df2$euro_mean_unk + train_df2$euro_mean_ret + train_df2$euro_mean_ser + train_df2$euro_mean_hou

####################

# TEST
# Creating Mean job
test_df2$euro_mean_admin[test_df2$job.admin. == 1] = mean(test_df2$euribor3m[test_df2$job.admin. == 1])
test_df2$euro_mean_admin[is.na(test_df2$euro_mean_admin)] = 0

test_df2$euro_mean_bc[test_df2$job.blue.collar == 1] = mean(test_df2$euribor3m[test_df2$job.blue.collar == 1])
test_df2$euro_mean_bc[is.na(test_df2$euro_mean_bc)] = 0

test_df2$euro_mean_u[test_df2$job.unemployed == 1] = mean(test_df2$euribor3m[test_df2$job.unemployed == 1])
test_df2$euro_mean_u[is.na(test_df2$euro_mean_u)] = 0

test_df2$euro_mean_t[test_df2$job.technician == 1] = mean(test_df2$euribor3m[test_df2$job.technician == 1])
test_df2$euro_mean_t[is.na(test_df2$euro_mean_t)] = 0

test_df2$euro_mean_stu[test_df2$job.student == 1] = mean(test_df2$euribor3m[test_df2$job.student == 1])
test_df2$euro_mean_stu[is.na(test_df2$euro_mean_stu)] = 0

test_df2$euro_mean_se[test_df2$job.self.employed == 1] = mean(test_df2$euribor3m[test_df2$job.self.employed == 1])
test_df2$euro_mean_se[is.na(test_df2$euro_mean_se)] = 0

test_df2$euro_mean_man[test_df2$job.management == 1] = mean(test_df2$euribor3m[test_df2$job.management == 1])
test_df2$euro_mean_man[is.na(test_df2$euro_mean_man)] = 0

test_df2$euro_mean_ent[test_df2$job.entrepreneur == 1] = mean(test_df2$euribor3m[test_df2$job.entrepreneur == 1])
test_df2$euro_mean_ent[is.na(test_df2$euro_mean_ent)] = 0

test_df2$euro_mean_unk[test_df2$job.unknown == 1] = mean(test_df2$euribor3m[test_df2$job.unknown == 1])
test_df2$euro_mean_unk[is.na(test_df2$euro_mean_unk)] = 0

test_df2$euro_mean_ret[test_df2$job.retired == 1] = mean(test_df2$euribor3m[test_df2$job.retired == 1])
test_df2$euro_mean_ret[is.na(test_df2$euro_mean_ret)] = 0

test_df2$euro_mean_ser[test_df2$job.services == 1] = mean(test_df2$euribor3m[test_df2$job.services == 1])
test_df2$euro_mean_ser[is.na(test_df2$euro_mean_ser)] = 0

test_df2$euro_mean_hou[test_df2$job.housemaid == 1] = mean(test_df2$euribor3m[test_df2$job.housemaid == 1])
test_df2$euro_mean_hou[is.na(test_df2$euro_mean_hou)] = 0

test_df2$euro_mean = test_df2$euro_mean_admin + test_df2$euro_mean_bc + test_df2$euro_mean_u + test_df2$euro_mean_t + test_df2$euro_mean_stu + test_df2$euro_mean_se + test_df2$euro_mean_man + test_df2$euro_mean_ent + test_df2$euro_mean_unk + test_df2$euro_mean_ret + test_df2$euro_mean_ser + test_df2$euro_mean_hou

Prince Index Marital Status:

In [22]:
# TRAIN
# Creating Mean marital
train_df2$cpi_marital_mean_div[train_df2$marital.divorced == 1] = mean(train_df2$cons.price.idx[train_df2$marital.divorced == 1])
train_df2$cpi_marital_mean_div[is.na(train_df2$cpi_marital_mean_div)] = 0

train_df2$cpi_marital_mean_sing[train_df2$marital.single == 1] = mean(train_df2$cons.price.idx[train_df2$marital.single == 1])
train_df2$cpi_marital_mean_sing[is.na(train_df2$cpi_marital_mean_sing)] = 0

train_df2$cpi_marital_mean_marr[train_df2$marital.married == 1] = mean(train_df2$cons.price.idx[train_df2$marital.married == 1])
train_df2$cpi_marital_mean_marr[is.na(train_df2$cpi_marital_mean_marr)] = 0

train_df2$cpi_marital_mean_un[train_df2$marital.unknown == 1] = mean(train_df2$cons.price.idx[train_df2$marital.un == 1])
train_df2$cpi_marital_mean_un[is.na(train_df2$cpi_marital_mean_un)] = 0

train_df2$cpi_marital_mean =train_df2$cpi_marital_mean_div + train_df2$cpi_marital_mean_sing+train_df2$cpi_marital_mean_marr+train_df2$cpi_marital_mean_un

####################

# TEST
# Creating Mean marital
test_df2$cpi_marital_mean_div[test_df2$marital.divorced == 1] = mean(test_df2$cons.price.idx[test_df2$marital.divorced == 1])
test_df2$cpi_marital_mean_div[is.na(test_df2$cpi_marital_mean_div)] = 0

test_df2$cpi_marital_mean_sing[test_df2$marital.single == 1] = mean(test_df2$cons.price.idx[test_df2$marital.single == 1])
test_df2$cpi_marital_mean_sing[is.na(test_df2$cpi_marital_mean_sing)] = 0

test_df2$cpi_marital_mean_marr[test_df2$marital.married == 1] = mean(test_df2$cons.price.idx[test_df2$marital.married == 1])
test_df2$cpi_marital_mean_marr[is.na(test_df2$cpi_marital_mean_marr)] = 0

test_df2$cpi_marital_mean_un[test_df2$marital.unknown == 1] = mean(test_df2$cons.price.idx[test_df2$marital.un == 1])
test_df2$cpi_marital_mean_un[is.na(test_df2$cpi_marital_mean_un)] = 0

test_df2$cpi_marital_mean =test_df2$cpi_marital_mean_div + test_df2$cpi_marital_mean_sing+test_df2$cpi_marital_mean_marr+test_df2$cpi_marital_mean_un

In [23]:
# TEST
# Creating Mean job
train_df2$euro_marital_mean_div[train_df2$marital.divorced == 1] = mean(train_df2$euribor3m[train_df2$marital.divorced == 1])
train_df2$euro_marital_mean_div[is.na(train_df2$euro_marital_mean_div)] = 0

train_df2$euro_marital_mean_sing[train_df2$marital.single == 1] = mean(train_df2$euribor3m[train_df2$marital.single == 1])
train_df2$euro_marital_mean_sing[is.na(train_df2$euro_marital_mean_sing)] = 0

train_df2$euro_marital_mean_marr[train_df2$marital.married == 1] = mean(train_df2$euribor3m[train_df2$marital.married == 1])
train_df2$euro_marital_mean_marr[is.na(train_df2$euro_marital_mean_marr)] = 0

train_df2$euro_marital_mean_un[train_df2$marital.unknown == 1] = mean(train_df2$euribor3m[train_df2$marital.un == 1])
train_df2$euro_marital_mean_un[is.na(train_df2$euro_marital_mean_un)] = 0

train_df2$euro_marital_mean =train_df2$euro_marital_mean_div + train_df2$euro_marital_mean_sing+train_df2$euro_marital_mean_marr+train_df2$euro_marital_mean_un

####################

# TEST
# Creating Mean job
test_df2$euro_marital_mean_div[test_df2$marital.divorced == 1] = mean(test_df2$euribor3m[test_df2$marital.divorced == 1])
test_df2$euro_marital_mean_div[is.na(test_df2$euro_marital_mean_div)] = 0

test_df2$euro_marital_mean_sing[test_df2$marital.single == 1] = mean(test_df2$euribor3m[test_df2$marital.single == 1])
test_df2$euro_marital_mean_sing[is.na(test_df2$euro_marital_mean_sing)] = 0

test_df2$euro_marital_mean_marr[test_df2$marital.married == 1] = mean(test_df2$euribor3m[test_df2$marital.married == 1])
test_df2$euro_marital_mean_marr[is.na(test_df2$euro_marital_mean_marr)] = 0

test_df2$euro_marital_mean_un[test_df2$marital.unknown == 1] = mean(test_df2$euribor3m[test_df2$marital.un == 1])
test_df2$euro_marital_mean_un[is.na(test_df2$euro_marital_mean_un)] = 0

test_df2$euro_marital_mean =test_df2$euro_marital_mean_div + test_df2$euro_marital_mean_sing+test_df2$euro_marital_mean_marr+test_df2$euro_marital_mean_un

Age_ge_mean by Age Segment:

In [24]:
#### Add variable: age > mean(age)
# Train
train_df2[, 'age_ge_mean'] = as.integer(train_df2$age > mean(train_df2$age))
# Test (holdout)
test_df2[, 'age_ge_mean'] = as.integer(test_df2$age > mean(test_df2$age))

Squared Variables:

In [25]:
# TRAIN
train_df2$euribor3m_sqr = (train_df2$euribor3m)^2
train_df2$emp.var.rate_sqr = (train_df2$emp.var.rate)^2
train_df2$cons.price.idx_sqr = (train_df2$cons.price.idx)^2

####################

# TEST
test_df2$euribor3m_sqr = (test_df2$euribor3m)^2
test_df2$emp.var.rate_sqr = (test_df2$emp.var.rate)^2
test_df2$cons.price.idx_sqr = (test_df2$cons.price.idx)^2

Cubic Variables:

In [26]:
# TRAIN
train_df2$euribor3m_cubic = (train_df2$euribor3m)^3
train_df2$emp.var.rate_cubic = (train_df2$emp.var.rate)^3
train_df2$cons.price.idx_cubic = (train_df2$cons.price.idx)^3

####################

# TEST
test_df2$euribor3m_cubic = (test_df2$euribor3m)^3
test_df2$emp.var.rate_cubic = (test_df2$emp.var.rate)^3
test_df2$cons.price.idx_cubic = (test_df2$cons.price.idx)^3

Combination Variables:

In [27]:
# TRAIN
train_df2$euribor3m_emp.var.rate = (train_df2$euribor3m)*(train_df2$emp.var.rate)
train_df2$euribor3m_cons.price.idx = (train_df2$euribor3m)*(train_df2$cons.price.idx)
train_df2$emp.var.rate_cons.price.idx = (train_df2$emp.var.rate)*(train_df2$cons.price.idx)
train_df2$emp.var.rate_cons.price.idx_euribor3m = (train_df2$emp.var.rate)*(train_df2$cons.price.idx)*(train_df2$euribor3m)

# TEST
test_df2$euribor3m_emp.var.rate = (test_df2$euribor3m)*(test_df2$emp.var.rate)
test_df2$euribor3m_cons.price.idx = (test_df2$euribor3m)*(test_df2$cons.price.idx)
test_df2$emp.var.rate_cons.price.idx = (test_df2$emp.var.rate)*(test_df2$cons.price.idx)
test_df2$emp.var.rate_cons.price.idx_euribor3m = (test_df2$emp.var.rate)*(test_df2$cons.price.idx)*(test_df2$euribor3m)

**f) Eliminating one dummy variable for each set:**

In [28]:
# Eliminating a dummy feature per original discrete feature 
# TRAIN
train_df2[c("marital.unknown","education.unknown","default.unknown","housing.unknown","loan.unknown",
           "contact.telephone","month.dec","day_of_week.fri","poutcome.nonexistent",
          "cons.price.idx_mean_1","cons.price.idx_mean_2","cons.price.idx_mean_3","cons.price.idx_mean_4",
          "cons.price.idx_mean_5","cons.price.idx_mean_6","euribor3m_mean_1","euribor3m_mean_2",
          "euribor3m_mean_3","euribor3m_mean_4","euribor3m_mean_5","euribor3m_mean_6","euribor3m_max_1",
          "euribor3m_max_2","euribor3m_max_3","euribor3m_max_4","euribor3m_max_5","euribor3m_max_6",
          "euribor3m_min_1","euribor3m_min_2","euribor3m_min_3","euribor3m_min_4","euribor3m_min_5",
          "euribor3m_min_6",'cpi_mean_admin','cpi_mean_bc','cpi_mean_u','cpi_mean_t','cpi_mean_stu','cpi_mean_se',
           'cpi_mean_man','cpi_mean_ent','cpi_mean_unk','cpi_mean_ret','cpi_mean_ser','cpi_mean_hou','cpi_mean',
          'euro_mean_admin','euro_mean_bc','euro_mean_u','euro_mean_t','euro_mean_stu','euro_mean_se','euro_mean_man',
           'euro_mean_ent','euro_mean_unk','euro_mean_ret','euro_mean_ser','euro_mean_hou',
          'cpi_marital_mean_div','cpi_marital_mean_sing','cpi_marital_mean_marr','cpi_marital_mean_un',
          'euro_marital_mean_div','euro_marital_mean_sing','euro_marital_mean_marr','euro_marital_mean_un',
           "campaign","pdays","previous","nr.employed","job.binned.unknown","winter","Q4","education.illiterate",
            "pdays.11to20","previous.1to3","emp.var.rate.neg")] = NULL

####################

# TEST
test_df2[c("marital.unknown","education.unknown","default.unknown","housing.unknown","loan.unknown",
           "contact.telephone","month.dec","day_of_week.fri","poutcome.nonexistent",
          "cons.price.idx_mean_1","cons.price.idx_mean_2","cons.price.idx_mean_3","cons.price.idx_mean_4",
          "cons.price.idx_mean_5","cons.price.idx_mean_6","euribor3m_mean_1","euribor3m_mean_2",
          "euribor3m_mean_3","euribor3m_mean_4","euribor3m_mean_5","euribor3m_mean_6","euribor3m_max_1",
          "euribor3m_max_2","euribor3m_max_3","euribor3m_max_4","euribor3m_max_5","euribor3m_max_6",
          "euribor3m_min_1","euribor3m_min_2","euribor3m_min_3","euribor3m_min_4","euribor3m_min_5",
          "euribor3m_min_6",'cpi_mean_admin','cpi_mean_bc','cpi_mean_u','cpi_mean_t','cpi_mean_stu','cpi_mean_se',
           'cpi_mean_man','cpi_mean_ent','cpi_mean_unk','cpi_mean_ret','cpi_mean_ser','cpi_mean_hou','cpi_mean',
          'euro_mean_admin','euro_mean_bc','euro_mean_u','euro_mean_t','euro_mean_stu','euro_mean_se','euro_mean_man',
           'euro_mean_ent','euro_mean_unk','euro_mean_ret','euro_mean_ser','euro_mean_hou',
          'cpi_marital_mean_div','cpi_marital_mean_sing','cpi_marital_mean_marr','cpi_marital_mean_un',
          'euro_marital_mean_div','euro_marital_mean_sing','euro_marital_mean_marr','euro_marital_mean_un',
           "campaign","pdays","previous","nr.employed","job.binned.unknown","winter","Q4",
            "pdays.11to20","previous.1to3","emp.var.rate.neg")] = NULL

**g) Final Dataframes:**

In [29]:
train_df = train_df2
test_df = test_df2

## 2) Features Selection

**a) Variable selection Function:**

In [30]:
FisherScore <- function(basetable, depvar, IV_list) {
  "
  This function calculate the Fisher score of a variable.
  
  Ref:
  ---
  Verbeke, W., Dejaeger, K., Martens, D., Hur, J., & Baesens, B. (2012). New insights into churn prediction in the telecommunication sector: A profit driven data mining approach. European Journal of Operational Research, 218(1), 211-229.
  "
  
  # Get the unique values of dependent variable
  DV <- unique(basetable[, depvar])
  
  IV_FisherScore <- c()
  
  for (v in IV_list) {
    fs <- abs((mean(basetable[which(basetable[, depvar]==DV[1]), v]) - mean(basetable[which(basetable[, depvar]==DV[2]), v]))) /
      sqrt((var(basetable[which(basetable[, depvar]==DV[1]), v]) + var(basetable[which(basetable[, depvar]==DV[2]), v])))
    IV_FisherScore <- c(IV_FisherScore, fs)
  }
  
  return(data.frame(IV=IV_list, fisher_score=IV_FisherScore))
}

varSelectionFisher <- function(basetable, depvar, IV_list, num_select=88) {
  "
  This function will calculate the Fisher score for all IVs and select the best
  top IVs.

  Assumption: all variables of input dataset are converted into numeric type.
  "
  
  fs <- FisherScore(basetable, depvar, IV_list)  # Calculate Fisher Score for all IVs
  num_select <- min(num_select, ncol(basetable))  # Top N IVs to be selected
  return(as.vector(fs[order(fs$fisher_score, decreasing=T), ][1:num_select, 'IV']))
}

**b) Selecting the most significant features:**

In [31]:
# Calculate Fisher Score for all variable
# Get the IV and DV list
dv_list <- c('subscribe')  # DV list
iv_list <- setdiff(names(train_df), dv_list)  # IV list excluded DV
iv_list <- setdiff(iv_list, 'client_id')  # Excluded the client_id
fs <- FisherScore(train_df, dv_list, iv_list)
head(fs)

IV               fisher_score
1 age              0.083990951 
2 job.admin.       0.041728549 
3 job.blue.collar  0.150207459 
4 job.entrepreneur 0.014422451 
5 job.housemaid    0.007634457 
6 job.management   0.002600352

In [32]:
best_fs_var <- varSelectionFisher(train_df, dv_list, iv_list, num_select=20)
best_fs_var

[1] "euribor3m"                            
 [2] "euribor3m_cons.price.idx"             
 [3] "emp.var.rate_cons.price.idx"          
 [4] "emp.var.rate"                         
 [5] "euribor3m_sqr"                        
 [6] "euribor3m_cubic"                      
 [7] "emp.var.rate.pos"                     
 [8] "emp.var.rate_cons.price.idx_euribor3m"
 [9] "euribor3m_emp.var.rate"               
[10] "emp.var.rate_cubic"                   
[11] "emp.var.rate_sqr"                     
[12] "pdays.999"                            
[13] "poutcome.success"                     
[14] "pdays.0to10"                          
[15] "contact.cellular"                     
[16] "cons.price.idx"                       
[17] "cons.price.idx_sqr"                   
[18] "cons.price.idx_cubic"                 
[19] "euribor3m_mean"                       
[20] "month.may"

In [33]:
# Pick out categorical and numerical variable
iv_cat_list <- c()  # List to store categorical variable
iv_num_list <- c()  # List to store numerical variable
for (v in iv_list) {
    if (class(train_df[, v]) == 'factor') {  # Factor == categorical variable
        iv_cat_list <- c(iv_cat_list, v)
    } else {  # Non-factor == numerical variable
        iv_num_list <- c(iv_num_list, v)
    }
}

**c) Applying variable selection on train and test (holdout):**

In [34]:
# Train
train_var_select <- names(train_df)[names(train_df) %in% best_fs_var]
train_processed <- train_df[, c('client_id', train_var_select, 'subscribe')]

# Test (holdout)
test_hd_var_select <- names(test_df)[names(test_df) %in% best_fs_var]
test_holdout_processed <- test_df[, c('client_id', test_hd_var_select)]

In [35]:
# Factorizing the dependet feature
train_processed2 = train_processed
train_processed2$subscribe = as.factor(train_processed2$subscribe)

In [36]:
# Downloading the output
write.csv(train_processed2, 'C:/Users/jpolancoroque/Desktop/IESEG/02. Second Semester/Statistical & Machine Learning Approaches for Marketing/train_processed2.csv', row.names=FALSE)
write.csv(test_holdout_processed, 'C:/Users/jpolancoroque/Desktop/IESEG/02. Second Semester/Statistical & Machine Learning Approaches for Marketing/test_holdout_processed.csv', row.names=FALSE)

## 3) Modeling

**a) Logistic Regression:**

In [37]:
# Set up cross-validation
rdesc = makeResampleDesc("CV", iters=10, predict="both")

# Define the model
learner <- makeLearner("classif.logreg", predict.type="prob", fix.factors.prediction=T)

# Define the task
train_task <- makeClassifTask(id="bank_train", data=train_processed2[, -1], target="subscribe")

# Set hyper parameter tuning
tune_params <- makeLogicalLearnerParam("model", default = TRUE, tunable = FALSE)
ctrl = makeTuneControlRandom(maxit = 100)

# Run the hyper parameter tuning with k-fold CV
if (length(tune_params$pars) > 0) {
    # Run parameter tuning
    res <- tuneParams(learner, task=train_task, resampling=rdesc,
      par.set=tune_params, control=ctrl, measures=list(mlr::auc))
    

    # Extract best model
    best_learner <- res$learner
    
} else {
    # Simple cross-validation
    res <- resample(learner, train_task, rdesc, measures=list(mlr::auc, setAggregation(mlr::auc, train.mean)))
    
    # No parameter for tuning, only 1 best learner
    best_learner <- learner
}

Resampling: cross-validation

Measures:             auc.train   auc.test    

[Resample] iter 1:    0.8030522   0.7608107   

[Resample] iter 2:    0.7958607   0.8397802   

[Resample] iter 3:    0.7961807   0.8276392   

[Resample] iter 4:    0.7968134   0.8218938   

[Resample] iter 5:    0.7983707   0.8081857   

[Resample] iter 6:    0.8031106   0.7639960   

[Resample] iter 7:    0.8011420   0.7852800   

[Resample] iter 8:    0.7998484   0.7920909   

[Resample] iter 9:    0.8062468   0.7505910   

[Resample] iter 10:   0.7972947   0.8180328   




Aggregated Result: auc.test.mean=0.7968300,auc.train.mean=0.7997920






In [38]:
# Retrain the model with tbe best hyper-parameters
best_md <- mlr::train(best_learner, train_task)

In [39]:
# Make prediction on test data
pred <- predict(best_md, newdata=test_df2[, -1])
pred

Prediction: 3000 observations
predict.type: prob
threshold: 0=0.50,1=0.50
time: 0.00
     prob.0     prob.1 response
1 0.9186746 0.08132544        0
2 0.9450513 0.05494867        0
3 0.7207268 0.27927320        0
4 0.9705208 0.02947924        0
5 0.9676988 0.03230122        0
6 0.9287586 0.07124143        0
... (#rows: 3000, #cols: 3)

In [209]:
# Downloading the output
output <- data.frame(client_id=test_df2$client_id, subscribe=pred$data$prob.1)

**b) Random Forest Model:**

In [40]:
# Set up cross-validation
rdesc = makeResampleDesc("CV", iters=5)

# Define the model
learner <- makeLearner("classif.randomForest", predict.type="prob", fix.factors.prediction=T)

# Define the task
train_task <- makeClassifTask(id="bank_train", data=train_processed2[, -1], target="subscribe")

# Set hyper parameter tuning
tune_params <- makeParamSet(
  makeDiscreteParam('ntree', value=c(100, 250, 500, 750, 1000)),
  makeDiscreteParam('mtry', value=round(sqrt((ncol(train_processed2)-1) * c(0.1, 0.25, 0.5, 1, 2, 4))))
)
ctrl = makeTuneControlRandom(maxit = 5)

# Run the hyper parameter tuning with k-fold CV
if (length(tune_params$pars) > 0) {
    # Run parameter tuning
    res <- tuneParams(learner, task=train_task, resampling=rdesc,
      par.set=tune_params, control=ctrl, measures=list(mlr::auc))
    
    # Extract best model
    best_learner <- res$learner
    
} else {
    # Simple cross-validation
    res <- resample(learner, train_task, rdesc, measures=list(mlr::auc))
    
    # No parameter for tuning, only 1 best learner
    best_learner <- learner
}

[Tune] Started tuning learner classif.randomForest for parameter set:

          Type len Def               Constr Req Tunable Trafo
ntree discrete   -   - 100,250,500,750,1000   -    TRUE     -
mtry  discrete   -   -          1,2,3,5,6,9   -    TRUE     -

With control class: TuneControlRandom

Imputation value: -0

[Tune-x] 1: ntree=750; mtry=9

[Tune-y] 1: auc.test.mean=0.7640086; time: 1.4 min

[Tune-x] 2: ntree=100; mtry=2

[Tune-y] 2: auc.test.mean=0.7636697; time: 0.1 min

[Tune-x] 3: ntree=250; mtry=6

[Tune-y] 3: auc.test.mean=0.7650057; time: 0.4 min

[Tune-x] 4: ntree=100; mtry=2

[Tune-y] 4: auc.test.mean=0.7635422; time: 0.1 min

[Tune-x] 5: ntree=1000; mtry=9

[Tune-y] 5: auc.test.mean=0.7645404; time: 1.8 min

[Tune] Result: ntree=250; mtry=6 : auc.test.mean=0.7650057



In [41]:
# Retrain the model with tbe best hyper-parameters
best_md <- mlr::train(best_learner, train_task)

In [42]:
# Make prediction on test data
pred <- predict(best_md, newdata=test_df2[, -1])
pred

Prediction: 3000 observations
predict.type: prob
threshold: 0=0.50,1=0.50
time: 0.20
  prob.0 prob.1 response
1  1.000  0.000        0
2  1.000  0.000        0
3  0.506  0.494        0
4  1.000  0.000        0
5  1.000  0.000        0
6  1.000  0.000        0
... (#rows: 3000, #cols: 3)

In [136]:
# Output predicted file
output <- data.frame(client_id=test_df2$client_id, subscribe=pred$data$prob.1)

**c) LDA Model:**

In [51]:
# Set up cross-validation
rdesc = makeResampleDesc("CV", iters=3, predict="both")

# Define the model
learner <- makeLearner("classif.lda", predict.type="prob", fix.factors.prediction=T)

# Define the task
train_task <- makeClassifTask(id="bank_train", data=train_processed2[, -1], target="subscribe")

# Set hyper parameter tuning
tune_params <- makeParamSet(
)
ctrl = makeTuneControlGrid()

# Run the hyper parameter tuning with k-fold CV
if (length(tune_params$pars) > 0) {
    # Run parameter tuning
    res <- tuneParams(learner, task=train_task, resampling=rdesc,
      par.set=tune_params, control=ctrl, measures=list(mlr::auc))
    

    # Extract best model
    best_learner <- res$learner
    
} else {
    # Simple cross-validation
    res <- resample(learner, train_task, rdesc, measures=list(mlr::auc, setAggregation(mlr::auc, train.mean)))
    
    # No parameter for tuning, only 1 best learner
    best_learner <- learner
}

Resampling: cross-validation

Measures:             auc.train   auc.test    

Warning message in lda.default(x, grouping, ...):
"variables are collinear"
[Resample] iter 1:    0.8126890   0.7694332   

Warning message in lda.default(x, grouping, ...):
"variables are collinear"
[Resample] iter 2:    0.7998889   0.7905680   

Warning message in lda.default(x, grouping, ...):
"variables are collinear"
[Resample] iter 3:    0.7820590   0.8265896   




Aggregated Result: auc.test.mean=0.7955303,auc.train.mean=0.7982123






In [52]:
# Retrain the model with tbe best hyper-parameters
best_md <- mlr::train(best_learner, train_task)

Warning message in lda.default(x, grouping, ...):
"variables are collinear"


In [53]:
# Make prediction on test data
pred <- predict(best_md, newdata=test_df2[, -1])
pred

Prediction: 3000 observations
predict.type: prob
threshold: 0=0.50,1=0.50
time: 0.00
     prob.0     prob.1 response
1 0.9619004 0.03809958        0
2 0.9770328 0.02296724        0
3 0.3927237 0.60727629        1
4 0.9895942 0.01040582        0
5 0.9826457 0.01735434        0
6 0.9718316 0.02816838        0
... (#rows: 3000, #cols: 3)

In [ ]:
# Output predicted file
output <- data.frame(client_id=test_df2$client_id, subscribe=pred$data$prob.1)

**d) Binomial Classifier Model:**

In [55]:
# Set up cross-validation
rdesc = makeResampleDesc("CV", iters=10, predict="both")

# Define the model
learner <- makeLearner("classif.binomial", predict.type="prob", fix.factors.prediction=T)

# Define the task
train_task <- makeClassifTask(id="bank_train", data=train_processed2[, -1], target="subscribe")

# Set hyper parameter tuning
tune_params <- makeParamSet(
)
ctrl = makeTuneControlGrid()

# Run the hyper parameter tuning with k-fold CV
if (length(tune_params$pars) > 0) {
    # Run parameter tuning
    res <- tuneParams(learner, task=train_task, resampling=rdesc,
      par.set=tune_params, control=ctrl, measures=list(mlr::auc))
    

    # Extract best model
    best_learner <- res$learner
    
} else {
    # Simple cross-validation
    res <- resample(learner, train_task, rdesc, measures=list(mlr::auc, setAggregation(mlr::auc, train.mean)))
    
    # No parameter for tuning, only 1 best learner
    best_learner <- learner
}

Resampling: cross-validation

Measures:             auc.train   auc.test    

[Resample] iter 1:    0.7989041   0.8107099   

[Resample] iter 2:    0.7996869   0.7879717   

[Resample] iter 3:    0.8007700   0.7877092   

[Resample] iter 4:    0.8015458   0.7836267   

[Resample] iter 5:    0.7978092   0.8161950   

[Resample] iter 6:    0.7989641   0.8003031   

[Resample] iter 7:    0.8011195   0.7871089   

[Resample] iter 8:    0.8011418   0.7834596   

[Resample] iter 9:    0.8006141   0.7889909   

[Resample] iter 10:   0.7974747   0.8141239   




Aggregated Result: auc.test.mean=0.7960199,auc.train.mean=0.7998030






In [56]:
# Retrain the model with tbe best hyper-parameters
best_md <- mlr::train(best_learner, train_task)

In [57]:
# Make prediction on test data
pred <- predict(best_md, newdata=test_df2[, -1])
pred

Prediction: 3000 observations
predict.type: prob
threshold: 0=0.50,1=0.50
time: 0.00
     prob.0     prob.1 response
1 0.9186746 0.08132544        0
2 0.9450513 0.05494867        0
3 0.7207268 0.27927320        0
4 0.9705208 0.02947924        0
5 0.9676988 0.03230122        0
6 0.9287586 0.07124143        0
... (#rows: 3000, #cols: 3)

In [ ]:
# Output predicted file
output <- data.frame(client_id=test_df2$client_id, subscribe=pred$data$prob.1)

**e) Bayesian Additive Regression Trees Model:**

In [58]:
# Set up cross-validation
rdesc = makeResampleDesc("CV", iters=10, predict="both")

# Define the model
learner <- makeLearner("classif.bartMachine", predict.type="prob", fix.factors.prediction=T)

# Define the task
train_task <- makeClassifTask(id="bank_train", data=train_processed2[, -1], target="subscribe")

# Set hyper parameter tuning
tune_params <- makeParamSet(
)
ctrl = makeTuneControlGrid()

# Run the hyper parameter tuning with k-fold CV
if (length(tune_params$pars) > 0) {
    # Run parameter tuning
    res <- tuneParams(learner, task=train_task, resampling=rdesc,
      par.set=tune_params, control=ctrl, measures=list(mlr::auc))
    

    # Extract best model
    best_learner <- res$learner
    
} else {
    # Simple cross-validation
    res <- resample(learner, train_task, rdesc, measures=list(mlr::auc, setAggregation(mlr::auc, train.mean)))
    
    # No parameter for tuning, only 1 best learner
    best_learner <- learner
}

Resampling: cross-validation

Measures:             auc.train   auc.test    



bartMachine initializing with 50 trees...
bartMachine vars checked...
bartMachine java init...
bartMachine factors created...
bartMachine before preprocess...
bartMachine after preprocess... 21 total features...
bartMachine sigsq estimated...
bartMachine training data finalized...
Now building bartMachine for classification ...Missing data feature ON. 
evaluating in sample data...done


[Resample] iter 1:    0.8092041   0.7990140   



bartMachine initializing with 50 trees...
bartMachine vars checked...
bartMachine java init...
bartMachine factors created...
bartMachine before preprocess...
bartMachine after preprocess... 21 total features...
bartMachine sigsq estimated...
bartMachine training data finalized...
Now building bartMachine for classification ...Missing data feature ON. 
evaluating in sample data...done


[Resample] iter 2:    0.8076144   0.8194211   



...

[Resample] iter 8:    0.8076929   0.8094108   



bartMachine initializing with 50 trees...
bartMachine vars checked...
bartMachine java init...
bartMachine factors created...
bartMachine before preprocess...
bartMachine after preprocess... 21 total features...
bartMachine sigsq estimated...
bartMachine training data finalized...
Now building bartMachine for classification ...Missing data feature ON. 
evaluating in sample data...done


[Resample] iter 9:    0.8138031   0.7899965   



bartMachine initializing with 50 trees...
bartMachine vars checked...
bartMachine java init...
bartMachine factors created...
bartMachine before preprocess...
bartMachine after preprocess... 21 total features...
bartMachine sigsq estimated...
bartMachine training data finalized...
Now building bartMachine for classification ...Missing data feature ON. 
evaluating in sample data...done


[Resample] iter 10:   0.8141104   0.7515356   




Aggregated Result: auc.test.mean=0.8010300,auc.train.mean=0.8101993






In [59]:
# Retrain the model with tbe best hyper-parameters
best_md <- mlr::train(best_learner, train_task)

bartMachine initializing with 50 trees...
bartMachine vars checked...
bartMachine java init...
bartMachine factors created...
bartMachine before preprocess...
bartMachine after preprocess... 21 total features...
bartMachine sigsq estimated...
bartMachine training data finalized...
Now building bartMachine for classification ...Missing data feature ON. 
evaluating in sample data...done


In [62]:
# Make prediction on test data
pred <- predict(best_md, newdata=test_df2[, -1])
pred

ERROR: Error in rbind(deparse.level, ...): numbers of columns of arguments do not match


In [65]:
# Output predicted file
output_bart <- data.frame(client_id=test_df2$client_id, subscribe=pred$data$prob.1)
write.csv(output_bart, 'C:/Users/jpolancoroque/Desktop/IESEG/02. Second Semester/Statistical & Machine Learning Approaches for Marketing/output_bart.csv', row.names=FALSE)

**f) Adabag Boosting Machine Model**

In [67]:
# Set up cross-validation
rdesc = makeResampleDesc("CV", iters=3, predict="both")

# Define the model
learner <- makeLearner("classif.boosting", predict.type="prob", fix.factors.prediction=T)

# Define the task
train_task <- makeClassifTask(id="bank_train", data=train_processed2[, -1], target="subscribe")

# Set hyper parameter tuning
tune_params <- makeParamSet(
)
ctrl = makeTuneControlGrid()

# Run the hyper parameter tuning with k-fold CV
if (length(tune_params$pars) > 0) {
    # Run parameter tuning
    res <- tuneParams(learner, task=train_task, resampling=rdesc,
      par.set=tune_params, control=ctrl, measures=list(mlr::auc))
    

    # Extract best model
    best_learner <- res$learner
    
} else {
    # Simple cross-validation
    res <- resample(learner, train_task, rdesc, measures=list(mlr::auc, setAggregation(mlr::auc, train.mean)))
    
    # No parameter for tuning, only 1 best learner
    best_learner <- learner
}

Resampling: cross-validation

Measures:             auc.train   auc.test    

[Resample] iter 1:    0.8135390   0.8215677   

[Resample] iter 2:    0.8363377   0.7817543   

[Resample] iter 3:    0.8361165   0.7868973   




Aggregated Result: auc.test.mean=0.7967398,auc.train.mean=0.8286644






In [68]:
# Retrain the model with tbe best hyper-parameters
best_md <- mlr::train(best_learner, train_task)

In [69]:
# Make prediction on test data
pred <- predict(best_md, newdata=test_df2[, -1])
pred

Prediction: 3000 observations
predict.type: prob
threshold: 0=0.50,1=0.50
time: 0.71
     prob.0     prob.1 response
1 0.8831458 0.11685416        0
2 0.9242009 0.07579911        0
3 0.7148098 0.28519019        0
4 0.8959227 0.10407726        0
5 0.8997320 0.10026795        0
6 0.8419475 0.15805254        0
... (#rows: 3000, #cols: 3)

In [87]:
# Output predicted file
output_gbm = data.frame(client_id=test_df2$client_id, subscribe=pred$data$prob.1)
write.csv(output_gbm, 'C:/Users/jpolancoroque/Desktop/IESEG/02. Second Semester/Statistical & Machine Learning Approaches for Marketing/output_output_gbm_2.csv', row.names=FALSE)

**g) Gradient Boosting Machine Model:**

In [73]:
# Set up cross-validation
rdesc = makeResampleDesc("CV", iters=5, predict="both")

# Define the model
learner <- makeLearner("classif.gbm", predict.type="prob", fix.factors.prediction=T)

# Define the task
train_task <- makeClassifTask(id="bank_train", data=train_processed2[, -1], target="subscribe")

# Set hyper parameter tuning
tune_params <- makeParamSet(
makeDiscreteLearnerParam(id = "distribution", default = "bernoulli", values = c("gaussian", "bernoulli", "adaboost", "poisson")),
makeIntegerParam("n.trees", lower = 100, upper = 1000), #number of trees
makeIntegerParam("interaction.depth", lower = 5, upper = 8), #depth of tree
makeNumericParam("shrinkage",lower = 0.01, upper = 0.01)

)
ctrl = makeTuneControlRandom(maxit = 5)


# Run the hyper parameter tuning with k-fold CV
if (length(tune_params$pars) > 0) {
    # Run parameter tuning
    res <- tuneParams(learner, task=train_task, resampling=rdesc,
      par.set=tune_params, control=ctrl, measures=list(mlr::auc))
    

    # Extract best model
    best_learner <- res$learner
    
} else {
    # Simple cross-validation
    res <- resample(learner, train_task, rdesc, measures=list(mlr::auc, setAggregation(mlr::auc, train.mean)))
    
    # No parameter for tuning, only 1 best learner
    best_learner <- learner
}

[Tune] Started tuning learner classif.gbm for parameter set:

                      Type len       Def                              Constr
distribution      discrete   - bernoulli gaussian,bernoulli,adaboost,poisson
n.trees            integer   -         -                        100 to 1e+03
interaction.depth  integer   -         -                              5 to 8
shrinkage          numeric   -         -                        0.01 to 0.01
                  Req Tunable Trafo
distribution        -    TRUE     -
n.trees             -    TRUE     -
interaction.depth   -    TRUE     -
shrinkage           -    TRUE     -

With control class: TuneControlRandom

Imputation value: -0

[Tune-x] 1: distribution=bernoulli; n.trees=435; interaction.depth=7; shrinkage=0.01

[Tune-y] 1: auc.test.mean=0.7999536; time: 0.5 min

[Tune-x] 2: distribution=gaussian; n.trees=882; interaction.depth=5; shrinkage=0.01

[Tune-y] 2: auc.test.mean=0.8004169; time: 0.7 min

[Tune-x] 3: distribution=poisson; n.

In [74]:
# Set up cross-validation
rdesc = makeResampleDesc("CV", iters=5, predict="both")

# Define the model
learner <- makeLearner("classif.gbm", predict.type="prob", fix.factors.prediction=T)

# Define the task
train_task <- makeClassifTask(id="bank_train", data=train_processed2[, -1], target="subscribe")

# Set hyper parameter tuning
tune_params <- makeParamSet(
makeDiscreteLearnerParam(id = "distribution", default = "bernoulli", values = c("gaussian", "bernoulli", "adaboost", "poisson")),
makeIntegerParam("n.trees", lower = 100, upper = 1000), #number of trees
makeIntegerParam("interaction.depth", lower = 5, upper = 8), #depth of tree
makeNumericParam("shrinkage",lower = 0.01, upper = 0.01)

)
ctrl = makeTuneControlRandom(maxit = 10)


# Run the hyper parameter tuning with k-fold CV
if (length(tune_params$pars) > 0) {
    # Run parameter tuning
    res <- tuneParams(learner, task=train_task, resampling=rdesc,
      par.set=tune_params, control=ctrl, measures=list(mlr::auc))
    

    # Extract best model
    best_learner <- res$learner
    
} else {
    # Simple cross-validation
    res <- resample(learner, train_task, rdesc, measures=list(mlr::auc, setAggregation(mlr::auc, train.mean)))
    
    # No parameter for tuning, only 1 best learner
    best_learner <- learner
}

[Tune] Started tuning learner classif.gbm for parameter set:

                      Type len       Def                              Constr
distribution      discrete   - bernoulli gaussian,bernoulli,adaboost,poisson
n.trees            integer   -         -                        100 to 1e+03
interaction.depth  integer   -         -                              5 to 8
shrinkage          numeric   -         -                        0.01 to 0.01
                  Req Tunable Trafo
distribution        -    TRUE     -
n.trees             -    TRUE     -
interaction.depth   -    TRUE     -
shrinkage           -    TRUE     -

With control class: TuneControlRandom

Imputation value: -0

[Tune-x] 1: distribution=poisson; n.trees=643; interaction.depth=5; shrinkage=0.01

[Tune-y] 1: auc.test.mean=0.7961242; time: 0.6 min

[Tune-x] 2: distribution=gaussian; n.trees=627; interaction.depth=8; shrinkage=0.01

[Tune-y] 2: auc.test.mean=0.7971884; time: 0.7 min

[Tune-x] 3: distribution=poisson; n.tr

In [71]:
# Retrain the model with tbe best hyper-parameters
best_md <- mlr::train(best_learner, train_task)

Distribution not specified, assuming bernoulli ...


In [72]:
# Make prediction on test data
pred <- predict(best_md, newdata=test_df2[, -1])
pred

Prediction: 3000 observations
predict.type: prob
threshold: 0=0.50,1=0.50
time: 0.01
      prob.1    prob.0 response
1 0.06680828 0.9331917        0
2 0.06124184 0.9387582        0
3 0.33171398 0.6682860        0
4 0.04321972 0.9567803        0
5 0.04080771 0.9591923        0
6 0.06340632 0.9365937        0
... (#rows: 3000, #cols: 3)